In [1]:
# Import all libraries needed for the tasks.
import requests
import pandas as pd
from pandas import ExcelFile
from pandas import ExcelWriter
from ast import literal_eval
import time
import requests
from retrying import retry
from confluent_kafka.admin import AdminClient, NewTopic
from confluent_kafka import Producer
from concurrent.futures import wait
import ujson
import json

In [2]:
def get_es_indices():
    '''See all elasticsearch indices
    '''
    r = requests.get("http://elasticsearch:9200/_cat/indices?format=json")
    if r.status_code != 200:
        print("Error listing indices")
        return None
    else:
        indices_full = r.json()  # contains full metadata as a dict
        indices = []  # let's extract the names separately
        for i in indices_full:
            indices.append(i['index'])
        return indices, indices_full
        
indices, indices_full = get_es_indices()
print(indices)

['recipes', 'shopping', 'testindex', '.kibana', 'citibike_index']


In [3]:
def create_es_index(index, index_config):
    '''Create and elasticsearch index
    '''
    r = requests.put("http://elasticsearch:9200/{}".format(index),
                     json=index_config)
    if r.status_code != 200:
        print("Error creating index")
    else:
        print("Index created")
        

def delete_es_index(index):
    r = requests.delete("http://elasticsearch:9200/{}".format(index))
    if r.status_code != 200:
        print("Error deleting index")
    else:
        print("Index deleted")

In [4]:
## Index configuration for the item descriptions and other fields
indices, indices_full = get_es_indices()
if 'shopping' in indices:
    delete_es_index('shopping')
    
index_config = {
    "mappings": {
        "purchase": {  # document TYPE
            "properties": {
                "InvoiceNo": {"type": "long"},
                "Description": {"type": "string", "index":"not_analyzed"},
                "UnitPrice": {"type": "double"},
                "Quantity": {"type": "long"},
                "Country": {"type": "string"},
                "InvoiceDate": {"type": "date"},
                "StringQuantity": {"type": "string", "index":"not_analyzed"},
                "StringPrice": {"type": "string", "index":"not_analyzed"},
            }
        }
    }
}

create_es_index('shopping', index_config)

Index deleted
Index created


In [5]:
def fling_message(index, doctype, msg):
    '''Send messages to elasticseach
    '''
    r = requests.post("http://elasticsearch:9200/{}/{}".format(index, doctype),
                      json=msg)
    if r.status_code != 201:
        print('Error sending message')
    else:
        print("message sent")

In [6]:
def execute_es_query(index, query):
    '''Query elasticsearch
    '''
    r = requests.get('http://elasticsearch:9200/{}/_search'.format(index),
                   json=query)
    if r.status_code != 200:
        print('Error with query')
        return None
    else:
        return r.json()

In [7]:
## Query to use for recommender.  
def query_purch_item(item):
    query_items = {
        'size': 0,
        "query": {
            "bool": {
                "filter": [
                    {"term":{"Description":item}}
                ]
            }
        },
        "aggs": {
            "topItems": {
                "significant_terms": {
                    "field": 'Description',
                    "exclude": [item],
                    "min_doc_count": 10
                }
            }
        }
    }
    res = execute_es_query('shopping',query_items)
    return(res)

In [8]:
## Import Kafka to consume messages
from confluent_kafka import Consumer, KafkaError

c = Consumer({'bootstrap.servers': 'kafka-1:9092',
              'group.id': 'citibike.test.consumer.2',
              'api.version.request': True,
              'log.connection.close': False,
              'socket.keepalive.enable': True,
              'session.timeout.ms': 6000,
              'default.topic.config': {'auto.offset.reset': 'smallest'}})

c.subscribe(['shopping'])

In [9]:
## Loop to pull all messages.  Takes about 30 seconds or so
x = 0
while True:
    msg = c.poll(timeout=10.0)  # same as c.consume, but returns only 1 message at a time
    
    if msg is None:  
        break
        print('Done')
    if msg.error():
        if msg.error().code() == KafkaError._PARTITION_EOF:
            continue
        else:    
            raise KafkaException(msg.error())
    
    else:
        message = json.loads(msg.value())
        fling_message('shopping','purchase',message) 
        x += 1
        print(x)

message sent
1
message sent
2
message sent
3
message sent
4
message sent
5
message sent
6
message sent
7
message sent
8
message sent
9
message sent
10
message sent
11
message sent
12
message sent
13
message sent
14
message sent
15
message sent
16
message sent
17
message sent
18
message sent
19
message sent
20
message sent
21
message sent
22
message sent
23
message sent
24
message sent
25
message sent
26
message sent
27
message sent
28
message sent
29
message sent
30
message sent
31
message sent
32
message sent
33
message sent
34
message sent
35
message sent
36
message sent
37
message sent
38
message sent
39
message sent
40
message sent
41
message sent
42
message sent
43
message sent
44
message sent
45
message sent
46
message sent
47
message sent
48
message sent
49
message sent
50
message sent
51
message sent
52
message sent
53
message sent
54
message sent
55
message sent
56
message sent
57
message sent
58
message sent
59
message sent
60
message sent
61
message sent
62
message sent
63
m

message sent
490
message sent
491
message sent
492
message sent
493
message sent
494
message sent
495
message sent
496
message sent
497
message sent
498
message sent
499
message sent
500
message sent
501
message sent
502
message sent
503
message sent
504
message sent
505
message sent
506
message sent
507
message sent
508
message sent
509
message sent
510
message sent
511
message sent
512
message sent
513
message sent
514
message sent
515
message sent
516
message sent
517
message sent
518
message sent
519
message sent
520
message sent
521
message sent
522
message sent
523
message sent
524
message sent
525
message sent
526
message sent
527
message sent
528
message sent
529
message sent
530
message sent
531
message sent
532
message sent
533
message sent
534
message sent
535
message sent
536
message sent
537
message sent
538
message sent
539
message sent
540
message sent
541
message sent
542
message sent
543
message sent
544
message sent
545
message sent
546
message sent
547
message sent
5

message sent
978
message sent
979
message sent
980
message sent
981
message sent
982
message sent
983
message sent
984
message sent
985
message sent
986
message sent
987
message sent
988
message sent
989
message sent
990
message sent
991
message sent
992
message sent
993
message sent
994
message sent
995
message sent
996
message sent
997
message sent
998
message sent
999
message sent
1000
message sent
1001
message sent
1002
message sent
1003
message sent
1004
message sent
1005
message sent
1006
message sent
1007
message sent
1008
message sent
1009
message sent
1010
message sent
1011
message sent
1012
message sent
1013
message sent
1014
message sent
1015
message sent
1016
message sent
1017
message sent
1018
message sent
1019
message sent
1020
message sent
1021
message sent
1022
message sent
1023
message sent
1024
message sent
1025
message sent
1026
message sent
1027
message sent
1028
message sent
1029
message sent
1030
message sent
1031
message sent
1032
message sent
1033
message sent
1

message sent
1442
message sent
1443
message sent
1444
message sent
1445
message sent
1446
message sent
1447
message sent
1448
message sent
1449
message sent
1450
message sent
1451
message sent
1452
message sent
1453
message sent
1454
message sent
1455
message sent
1456
message sent
1457
message sent
1458
message sent
1459
message sent
1460
message sent
1461
message sent
1462
message sent
1463
message sent
1464
message sent
1465
message sent
1466
message sent
1467
message sent
1468
message sent
1469
message sent
1470
message sent
1471
message sent
1472
message sent
1473
message sent
1474
message sent
1475
message sent
1476
message sent
1477
message sent
1478
message sent
1479
message sent
1480
message sent
1481
message sent
1482
message sent
1483
message sent
1484
message sent
1485
message sent
1486
message sent
1487
message sent
1488
message sent
1489
message sent
1490
message sent
1491
message sent
1492
message sent
1493
message sent
1494
message sent
1495
message sent
1496
message se

message sent
1898
message sent
1899
message sent
1900
message sent
1901
message sent
1902
message sent
1903
message sent
1904
message sent
1905
message sent
1906
message sent
1907
message sent
1908
message sent
1909
message sent
1910
message sent
1911
message sent
1912
message sent
1913
message sent
1914
message sent
1915
message sent
1916
message sent
1917
message sent
1918
message sent
1919
message sent
1920
message sent
1921
message sent
1922
message sent
1923
message sent
1924
message sent
1925
message sent
1926
message sent
1927
message sent
1928
message sent
1929
message sent
1930
message sent
1931
message sent
1932
message sent
1933
message sent
1934
message sent
1935
message sent
1936
message sent
1937
message sent
1938
message sent
1939
message sent
1940
message sent
1941
message sent
1942
message sent
1943
message sent
1944
message sent
1945
message sent
1946
message sent
1947
message sent
1948
message sent
1949
message sent
1950
message sent
1951
message sent
1952
message se

...

message sent
18536
message sent
18537
message sent
18538
message sent
18539
message sent
18540
message sent
18541
message sent
18542
message sent
18543
message sent
18544
message sent
18545
message sent
18546
message sent
18547
message sent
18548
message sent
18549
message sent
18550
message sent
18551
message sent
18552
message sent
18553
message sent
18554
message sent
18555
message sent
18556
message sent
18557
message sent
18558
message sent
18559
message sent
18560
message sent
18561
message sent
18562
message sent
18563
message sent
18564
message sent
18565
message sent
18566
message sent
18567
message sent
18568
message sent
18569
message sent
18570
message sent
18571
message sent
18572
message sent
18573
message sent
18574
message sent
18575
message sent
18576
message sent
18577
message sent
18578
message sent
18579
message sent
18580
message sent
18581
message sent
18582
message sent
18583
message sent
18584
message sent
18585
message sent
18586
message sent
18587
message sent

message sent
18972
message sent
18973
message sent
18974
message sent
18975
message sent
18976
message sent
18977
message sent
18978
message sent
18979
message sent
18980
message sent
18981
message sent
18982
message sent
18983
message sent
18984
message sent
18985
message sent
18986
message sent
18987
message sent
18988
message sent
18989
message sent
18990
message sent
18991
message sent
18992
message sent
18993
message sent
18994
message sent
18995
message sent
18996
message sent
18997
message sent
18998
message sent
18999
message sent
19000
message sent
19001
message sent
19002
message sent
19003
message sent
19004
message sent
19005
message sent
19006
message sent
19007
message sent
19008
message sent
19009
message sent
19010
message sent
19011
message sent
19012
message sent
19013
message sent
19014
message sent
19015
message sent
19016
message sent
19017
message sent
19018
message sent
19019
message sent
19020
message sent
19021
message sent
19022
message sent
19023
message sent

message sent
19408
message sent
19409
message sent
19410
message sent
19411
message sent
19412
message sent
19413
message sent
19414
message sent
19415
message sent
19416
message sent
19417
message sent
19418
message sent
19419
message sent
19420
message sent
19421
message sent
19422
message sent
19423
message sent
19424
message sent
19425
message sent
19426
message sent
19427
message sent
19428
message sent
19429
message sent
19430
message sent
19431
message sent
19432
message sent
19433
message sent
19434
message sent
19435
message sent
19436
message sent
19437
message sent
19438
message sent
19439
message sent
19440
message sent
19441
message sent
19442
message sent
19443
message sent
19444
message sent
19445
message sent
19446
message sent
19447
message sent
19448
message sent
19449
message sent
19450
message sent
19451
message sent
19452
message sent
19453
message sent
19454
message sent
19455
message sent
19456
message sent
19457
message sent
19458
message sent
19459
message sent

message sent
19846
message sent
19847
message sent
19848
message sent
19849
message sent
19850
message sent
19851
message sent
19852
message sent
19853
message sent
19854
message sent
19855
message sent
19856
message sent
19857
message sent
19858
message sent
19859
message sent
19860
message sent
19861
message sent
19862
message sent
19863
message sent
19864
message sent
19865
message sent
19866
message sent
19867
message sent
19868
message sent
19869
message sent
19870
message sent
19871
message sent
19872
message sent
19873
message sent
19874
message sent
19875
message sent
19876
message sent
19877
message sent
19878
message sent
19879
message sent
19880
message sent
19881
message sent
19882
message sent
19883
message sent
19884
message sent
19885
message sent
19886
message sent
19887
message sent
19888
message sent
19889
message sent
19890
message sent
19891
message sent
19892
message sent
19893
message sent
19894
message sent
19895
message sent
19896
message sent
19897
message sent

message sent
20286
message sent
20287
message sent
20288
message sent
20289
message sent
20290
message sent
20291
message sent
20292
message sent
20293
message sent
20294
message sent
20295
message sent
20296
message sent
20297
message sent
20298
message sent
20299
message sent
20300
message sent
20301
message sent
20302
message sent
20303
message sent
20304
message sent
20305
message sent
20306
message sent
20307
message sent
20308
message sent
20309
message sent
20310
message sent
20311
message sent
20312
message sent
20313
message sent
20314
message sent
20315
message sent
20316
message sent
20317
message sent
20318
message sent
20319
message sent
20320
message sent
20321
message sent
20322
message sent
20323
message sent
20324
message sent
20325
message sent
20326
message sent
20327
message sent
20328
message sent
20329
message sent
20330
message sent
20331
message sent
20332
message sent
20333
message sent
20334
message sent
20335
message sent
20336
message sent
20337
message sent

# Run until here
## Next we will run elasticsearch queries

In [10]:
## Test cell to look for top 5 recommended items with whatever product
## entered.  
best_items = query_purch_item('HANGING METAL HEART LANTERN')
recommended_items = [(best_items['aggregations']['topItems']['buckets'][0]['key']),
                    (best_items['aggregations']['topItems']['buckets'][1]['key']),
                    (best_items['aggregations']['topItems']['buckets'][2]['key']),
                    (best_items['aggregations']['topItems']['buckets'][3]['key']),
                    (best_items['aggregations']['topItems']['buckets'][4]['key'])]
recommended_items

['HANGING METAL STAR LANTERN',
 'LOVEBIRD HANGING DECORATION WHITE ',
 'GREEN ROSE WASHBAG',
 'IVORY HANGING DECORATION  HEART',
 'SCOTTIE DOGS BABY BIB']

In [11]:
## Re-import the data and run all transformations to be used for 
## recommender testing and validation.

dfe = pd.ExcelFile('Online Retail.xlsx')

df_base = dfe.parse('Online Retail')
df_base = df_base.sort_values(['InvoiceDate'],ascending = 1)

baskets = df_base.groupby('InvoiceNo')['Description'].apply(list)
baskets = baskets.to_frame()

basket_tot_price = df_base.groupby('InvoiceNo')['UnitPrice'].agg('sum')
basket_tot_price = basket_tot_price.to_frame()

basket_tot_items = df_base.groupby('InvoiceNo')['Quantity'].agg('sum')
basket_tot_items = basket_tot_items.to_frame()
basket_tot_items = basket_tot_items.rename(columns = {0:'TotalItems'})

country = df_base.groupby('InvoiceNo').apply(lambda x: x['Country'].unique())
country = country.to_frame()
country = country.rename(columns = {0:'Country'})

purch_date = df_base.groupby('InvoiceNo').apply(lambda x: x['InvoiceDate'].unique())
purch_date = purch_date.to_frame()
purch_date = purch_date.rename(columns = {0:'InvoiceDate'})

df_base['StringQuantity'] = df_base['Quantity'].apply(lambda x: str(x))
df_base['StringPrice'] = df_base['UnitPrice'].apply(lambda x: str(x))

quantities = df_base.groupby('InvoiceNo')['StringQuantity'].apply(list)
quantities = quantities.to_frame()
prices = df_base.groupby('InvoiceNo')['StringPrice'].apply(list)
prices = prices.to_frame()

messages = 0
messages = baskets.join(basket_tot_price)
messages = messages.join(basket_tot_items)
messages = messages.join(country)
messages = messages.join(purch_date)
messages = messages.join(quantities)
messages = messages.join(prices)

messages.reset_index(level = 0, inplace=True)



In [12]:
## Split the final dataset into train and test
messages_train = messages.iloc[0:(int(messages['Country'].count()*.8))]
messages_test = messages.iloc[(int(messages['Country'].count()*.8)+1):]

In [13]:
## Pull out items from item description
messages_test.reset_index(level = 0, inplace = True)
mess_test_items = messages_test['Description']   

In [14]:
## Pull each field out for a full list
test_items = {}
for fields in mess_test_items:
    for i, f in enumerate(fields):
        test_items[i] = f

In [15]:
## Make a new test set that includes the purchased item and top 5
## recommended items 
columns = ['item','rec1','rec2','rec3','rec4','rec5']
comparison = pd.DataFrame(columns = columns, index = range(100000))

In [16]:
## Run the recommender to populate the grid with information.
for i in test_items.keys():
    best_items = query_purch_item(test_items[i])                                     
    comparison.iloc[i]['item'] = test_items[i]
    try:
        comparison.iloc[i]['rec1'] = (best_items['aggregations']['topItems']['buckets'][0]['key'])
    except IndexError:
        comparison.iloc[i]['rec1'] = 0
    try:
        comparison.iloc[i]['rec2'] = (best_items['aggregations']['topItems']['buckets'][1]['key'])
    except IndexError:
        comparison.iloc[i]['rec2'] = 0
    try:
        comparison.iloc[i]['rec3'] = (best_items['aggregations']['topItems']['buckets'][2]['key'])
    except IndexError:
        comparison.iloc[i]['rec3'] = 0
    try:
        comparison.iloc[i]['rec4'] = (best_items['aggregations']['topItems']['buckets'][3]['key'])
    except IndexError:
        comparison.iloc[i]['rec4'] = 0
    try:
        comparison.iloc[i]['rec5'] = (best_items['aggregations']['topItems']['buckets'][4]['key'])
    except IndexError:
        comparison.iloc[i]['rec5'] = 0

In [17]:
## Look at the top rows to see what is most recommended with each item
comparison.head()

item                              rec1  \
0  HANGING HEART JAR T-LIGHT HOLDER  SINGLE HEART ZINC T-LIGHT HOLDER   
1     36 PENCILS TUBE RED RETROSPOT            36 PENCILS TUBE SKULLS   
2      RED RETROSPOT SMALL MILK JUG      RED RETROSPOT SUGAR JAM BOWL   
3    STRAWBERRY CERAMIC TRINKET POT    ANGEL DECORATION PAINTED ZINC    
4  SET 3 RETROSPOT TEA,COFFEE,SUGAR            RED SPOTTY BISCUIT TIN   

                                rec2                                rec3  \
0  HANGING HEART ZINC T-LIGHT HOLDER                      DOTCOM POSTAGE   
1           36 PENCILS TUBE WOODLAND            CANDY SPOT CUSHION COVER   
2           RETROSPOT LARGE MILK JUG           RED RETROSPOT BUTTER DISH   
3         NOEL GARLAND PAINTED ZINC   3 RAFFIA RIBBONS VINTAGE CHRISTMAS   
4                     DOTCOM POSTAGE     SET/2 RED RETROSPOT TEA TOWELS    

                                 rec4                               rec5  
0  BEADED CRYSTAL HEART PINK ON STICK       CRAZY DAISY HEART DECORATION  
1                  CARD SUKI BIRTHDAY                 SKULL SHOULDER BAG  
2                   RED RETROSPOT MUG  RED RETROSPOT TEA CUP AND SAUCER   
3         CHRISTMAS MUSICAL ZINC STAR      STAR DECORATION PAINTED ZINC   
4       RED RETROSPOT ROUND CAKE TINS            KINGS CHOICE TEA CADDY

In [18]:
messages_test.head()

index InvoiceNo                                        Description  \
0  20721    578817  [KEY FOB , SHED, KITCHEN METAL SIGN, BATHROOM ...   
1  20722    578818  [VICTORIAN SEWING KIT, CHICK GREY HOT WATER BO...   
2  20723    578819  [SET OF 3 HANGING OWLS OLLIE BEAK, JUMBO SHOPP...   
3  20724    578820  [RABBIT NIGHT LIGHT, FULL ENGLISH BREAKFAST PL...   
4  20725    578821  [BAKING SET SPACEBOY DESIGN, FAMILY PHOTO FRAM...   

   UnitPrice  Quantity           Country                      InvoiceDate  \
0     149.12       128  [United Kingdom]  [2011-11-25T13:45:00.000000000]   
1      73.01        74  [United Kingdom]  [2011-11-25T13:47:00.000000000]   
2      38.04       508  [United Kingdom]  [2011-11-25T13:52:00.000000000]   
3      11.02       152  [United Kingdom]  [2011-11-25T13:58:00.000000000]   
4      17.15        80  [United Kingdom]  [2011-11-25T13:59:00.000000000]   

                                      StringQuantity  \
0  [1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 4, 4, 4, 1, 2, ...   
1  [1, 2, 1, 2, 2, 3, 1, 1, 3, 1, 1, 1, 2, 2, 5, ...   
2          [192, 100, 100, 100, 6, 2, 2, 2, 1, 1, 2]   
3                                   [48, 16, 40, 48]   
4                                       [50, 20, 10]   

                                         StringPrice  
0  [0.65, 0.55, 0.55, 0.55, 2.95, 0.65, 1.65, 5.9...  
1  [1.25, 4.25, 1.95, 0.42, 1.95, 0.85, 9.95, 5.9...  
2  [1.04, 1.79, 1.79, 1.79, 2.08, 4.25, 3.75, 1.2...  
3                           [1.79, 3.39, 2.55, 3.29]  
4                                 [4.25, 9.95, 2.95]

In [19]:
## Next I hoped to create a measure of recommender performance.  
## This breaks out the baskets into individual strings
messages_test['liststring'] = [','.join(map(str, l)) for l in messages_test.Description]

/home/vagrant/miniconda3/envs/py37/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [24]:
# Remove duplicates to see what is recommended vs how often it is actually purchased
## Limit to the first recommendation.
test_success = comparison
test_success = test_success.drop(columns = ['rec2','rec3','rec4','rec5'])
test_success = test_success.drop_duplicates()
test_success.head()

item                              rec1
0  HANGING HEART JAR T-LIGHT HOLDER  SINGLE HEART ZINC T-LIGHT HOLDER
1     36 PENCILS TUBE RED RETROSPOT            36 PENCILS TUBE SKULLS
2      RED RETROSPOT SMALL MILK JUG      RED RETROSPOT SUGAR JAM BOWL
3    STRAWBERRY CERAMIC TRINKET POT    ANGEL DECORATION PAINTED ZINC 
4  SET 3 RETROSPOT TEA,COFFEE,SUGAR            RED SPOTTY BISCUIT TIN

In [64]:
## This is an attempt to measure the overall accuracy of the recommender on test data.  
## Information would not write to a new dataframe column, so this measures the success of recommendation
## the code will identify all occurrences of the purchase item in the test data 'baskets'
## It will then count the number of occurrences of the recommended item in the same cart and divide it by the total
## number of the purchased items found.  This creates a decimal for percentage of time that the recommended
## item is actually found in the test data baskets.  
test_success = comparison
test_success = test_success.drop(columns = ['rec2','rec3','rec4','rec5'])
test_success = test_success.drop_duplicates()
test_success.reset_index(level = 0, inplace=True)
val = [0.00]
for x in (test_success.index):
    item1 = str(test_success.iloc[x]['item'])
    rec1 = str(test_success.iloc[x]['rec1'])
    tot1 = messages_test.loc[(messages_test.liststring.str.contains(item1)), 'liststring'].count()
    success1 = messages_test.loc[(messages_test.liststring.str.contains(item1)) &
		  (messages_test.liststring.str.contains(rec1)), 'liststring'].count()
    val.extend([(success1/tot1)])

[0.0, 0.12307692307692308]
[0.0, 0.12307692307692308, 0.3783783783783784]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.0204

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727]
[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727, 0.5909090909090909, 0.08571428571428572, 0.375, 0.25, 0.42857142857142855, 

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727, 0.5909090909090909, 0.08571428571428572, 0.375, 0.25, 0.42857142857142855, 

...

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727, 0.5909090909090909, 0.08571428571428572, 0.375, 0.25, 0.42857142857142855, 

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727, 0.5909090909090909, 0.08571428571428572, 0.375, 0.25, 0.42857142857142855, 

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727, 0.5909090909090909, 0.08571428571428572, 0.375, 0.25, 0.42857142857142855, 

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727, 0.5909090909090909, 0.08571428571428572, 0.375, 0.25, 0.42857142857142855, 

[0.0, 0.12307692307692308, 0.3783783783783784, 0.23333333333333334, 0.02040816326530612, 0.4166666666666667, 0.32142857142857145, 0.75, 0.15384615384615385, 0.25, 0.16, 0.3, 0.125, 0.2631578947368421, 0.4222222222222222, 0.23076923076923078, 0.38636363636363635, 0.5846153846153846, 0.0, 0.6831683168316832, 0.73, 0.7222222222222222, 0.4, 0.5909090909090909, 0.5, 0.2857142857142857, 0.5185185185185185, 0.0, 0.25, 0.5454545454545454, 0.4827586206896552, 0.4838709677419355, 0.575, 0.22413793103448276, 0.6984126984126984, 0.5441176470588235, 0.4444444444444444, 0.5490196078431373, 0.5517241379310345, 0.7777777777777778, 0.5151515151515151, 0.2222222222222222, 0.4, 0.0, 0.03333333333333333, 0.2857142857142857, 0.16666666666666666, 0.14285714285714285, 0.5, 0.6, 0.5555555555555556, 0.0, 0.4, 0.1111111111111111, 0.0, 0.30303030303030304, 0.21052631578947367, 0.47619047619047616, 0.2608695652173913, 0.22727272727272727, 0.5909090909090909, 0.08571428571428572, 0.375, 0.25, 0.42857142857142855, 

In [72]:
## calculate the mean of the overall list after removing nan's
## NOTE this has not be tested thoroughly due to time constraints
import numpy as np
cleanval = [x for x in val if str(x) != 'nan']
np.mean(cleanval)

0.40104227367608775